# Eff. matching to GEN particle


   * [Efficiency vs $\eta$](#Effinciency-vs-$\eta$)
   * [Efficiency vs $p_{T}$](#Efficiency-vs-$p_{T}$)
   * [Turn-on curves](#Turn-on-curves)


In [1]:
import sys
sys.path.insert(0, '..')
import ROOT
import root_numpy as rnp
import python.l1THistos as histos
import math
import uuid
import pandas as pd

ROOT.enableJSVis()
#ROOT.enableJSVis()

#from drawingTools import *

normalized_histos = list()
    

Welcome to JupyROOT 6.14/02


In [118]:
import ROOT
import math
import uuid

# some useful globals, mainly to deal with ROOT idiosyncrasies
c_idx = 0
p_idx = 0
colors = range(1, 6)
stuff = []
f_idx = 0

ROOT.gStyle.SetOptTitle(False)
ROOT.gStyle.SetPadBottomMargin(0.13)
ROOT.gStyle.SetPadLeftMargin(0.13)
ROOT.gStyle.SetPadRightMargin(0.13)

# ROOT.gStyle.SetCanvasBorderMode(0)
# ROOT.gStyle.SetCanvasColor(0)


def getText(text, ndc_x, ndc_y):
    global stuff
    rtext = ROOT.TLatex(ndc_x, ndc_y, text)
    stuff.append(rtext)
    rtext.SetNDC(True)
    # rtext.SetTextFont(40)
    rtext.SetTextSize(0.03)
    return rtext

def getLegend(x1=0.7, y1=0.71, x2=0.95, y2=0.85):
    global stuff
    legend = ROOT.TLegend(x1, y1, x2, y2)
    stuff.append(legend)
    legend.SetFillColor(0)
    legend.SetFillStyle(0)
    legend.SetBorderSize(0)
    legend.SetTextSize(0.05)
    return legend

def newCanvas(name=None, title=None, height=600, width=800, xdiv=0, ydiv=0, form=4):
    global c_idx
    if name is None:
        name = 'c_{}'.format(uuid.uuid4().hex[:6])
        c_idx += 1
    if title is None:
        title = name
    print name, title, width, height
    canvas = ROOT.TCanvas(name, title, width, height)
    if(xdiv*ydiv != 0):
        canvas.Divide(xdiv, ydiv)
    global stuff
    stuff.append(canvas)
    return canvas

def drawAndProfileX(plot2d, miny=None, maxy=None, do_profile=True, options='', text=None):
    global p_idx
    if miny and maxy:
        plot2d.GetYaxis().SetRangeUser(miny, maxy)
    c = newCanvas()
    c.SetGrid(1, 1)
    c.cd()
    plot2d.Draw(options)
    ROOT.gPad.SetGrid(1, 1)
    ROOT.gStyle.SetGridColor(15)

    if do_profile:
        profname = plot2d.GetName()+'_prof_'+str(p_idx)
        p_idx += 1
        firstbin = 1
        lastbin = -1
        prof = plot2d.ProfileX(profname, firstbin, lastbin, 's')
        prof.SetMarkerColor(2)
        prof.SetLineColor(2)
        prof.Draw('same')

    if text:
        rtext = getText(text, 0.15, 0.85)
        rtext.Draw('same')

    c.Draw()


def draw(histograms,
         labels,
         options='',
         norm=False,
         logy=False,
         min_y=None,
         max_y=None,
         text=None,
         y_axis_label=None,
         x_axis_label=None,
         v_lines=None,
         h_lines=None,
         do_stats=False,
         do_profile=False,
         do_ratio=False):
    global colors
    global stuff
    global p_idx

    
    # 0 - determine kind and # of histos
    n_histos = len(histograms)
    if n_histos == 0:
        print '[draw]**ERROR: empy histo list'
        return

    histo_class = histograms[0].ClassName()

    # 1 - check argument consisntency
    if 'TH2' not in histo_class and do_profile:
        print '[draw]**ERROR: do_profile set for histo of class: {}'.format(histo_class)
        return

    # TH1 histograms are overlayed
    # TH2 histograms are drawn side by side in the same canvas
    overlay = True
    if n_histos > 1:
        if 'TH2' in histo_class or 'TH3' in histo_class:
            overlay = False

    # 2 - determine canvas properties
    xdiv = 0
    ydiv = 0
    c_width = 800
    c_height = 600
    # do_ratio = False

    if do_ratio:
        c_height = 800

    if not overlay:
        xdiv = 2
        c_width = 1000.
        ydiv = math.ceil(float(n_histos)/2)
        c_height = 500*ydiv
    canvas = newCanvas(name=None,
                       title=None,
                       height=int(c_height),
                       width=int(c_width),
                       xdiv=int(xdiv),
                       ydiv=int(ydiv))
    if overlay:
        canvas.SetRightMargin(0.30)

    canvas.cd()
    leg = getLegend()

    drawn_histos = []
    # drawn_histos = histograms
    for hidx, hist in enumerate(histograms):
        if 'TGraph' not in histo_class:
            hist.SetStats(do_stats)
        opt = options
        if overlay:
            hist.SetLineColor(colors[hidx])
            if hidx:
                opt = 'same,'+options
            else:
                if 'TGraph' in histo_class:
                    opt = options+'PA'
        else:
            canvas.cd(hidx+1)
        print hidx, opt
        d_hist = hist
        if norm:
            d_hist = hist.DrawNormalized(opt, 1.)
        else:
            hist.Draw(opt)

        if do_profile:
            profname = d_hist.GetName()+'_prof_'+str(p_idx)
            p_idx += 1
            firstbin = 1
            lastbin = -1
            prof = d_hist.ProfileX(profname, firstbin, lastbin, 's')
            prof.SetMarkerColor(2)
            prof.SetLineColor(2)
            prof.Draw('same')

        if overlay:
            leg.AddEntry(hist, labels[hidx], 'l')
        else:
            if text:
                newtext = '{}: {}'.format(labels[hidx], text)
                rtext = getText(newtext, 0.15, 0.85)
                rtext.Draw('same')
        drawn_histos.append(d_hist)

    if do_ratio:
        h_ratio = ROOT.TRatioPlot(drawn_histos[0], drawn_histos[1])
        stuff.append(h_ratio)
        h_ratio.Draw()

        pad = canvas.cd(1)
        h_ratio.GetUpperPad().SetBottomMargin(0)
        h_ratio.GetUpperPad().SetRightMargin(0.3)
        if logy:
            h_ratio.GetUpperPad().SetLogy()
        pad.Update()
        pad = canvas.cd(2)
        h_ratio.GetLowerPad().SetTopMargin(0)
        h_ratio.GetLowerPad().SetRightMargin(0.3)
        pad.Update()
        # hratio.GetLowerRefGraph().GetYaxis().SetRangeUser(-6, 6)

    canvas.Update()

    # we now set the axis properties
    max_value = max_y
    min_value = min_y

    if min_y is None:
        min_value = min([hist.GetBinContent(hist.GetMinimumBin()) for hist in drawn_histos])
    if max_y is None:
        max_value = max([hist.GetBinContent(hist.GetMaximumBin()) for hist in drawn_histos])*1.2
    print min_value, max_value

    for hist in drawn_histos:
        hist.GetYaxis().SetRangeUser(min_value, max_value)
        if y_axis_label:
            hist.GetYaxis().SetTitle(y_axis_label)
        if x_axis_label:
            hist.GetXaxis().SetTitle(x_axis_label)

    canvas.Draw()

    # we draw additional stuff if needed
    if overlay:
        canvas.cd()
        leg.Draw()
        if text:
            rtext = getText(text, 0.15, 0.85)
            rtext.Draw("same")

    pad_range = range(0, 1)
    if not overlay:
        pad_range = range(1, len(histograms)+1)

    for pad_id in pad_range:
        canvas.cd(pad_id)
        if v_lines:
            for v_line_x in v_lines:
                aline = ROOT.TLine(v_line_x, ROOT.gPad.GetUymin(), v_line_x,  ROOT.gPad.GetUymax())
                aline.SetLineStyle(2)
                aline.Draw("same")
                stuff.append(aline)
        if h_lines:
            for h_line_y in h_lines:
                aline = ROOT.TLine(ROOT.gPad.GetUxmin(), h_line_y, ROOT.gPad.GetUxmax(),  h_line_y)
                aline.SetLineStyle(2)
                aline.Draw("same")
                stuff.append(aline)
        if logy:
            if not do_ratio:
                ROOT.gPad.SetLogy()                

        ROOT.gPad.Update()
    canvas.Update()
    canvas.Draw()

    return canvas




In [64]:
h = ROOT.TH1F('t','t', 10,0,10)
h1 = ROOT.TH1F('t1','t1', 2,1,3)
h2 = ROOT.TH1F('t2','t2', 2,1,3)
h3 = ROOT.TH2F('t3','t3', 10,0,10,10,0,10)
h4 = ROOT.TH2F('t4','t4', 10,0,10, 10,0,10)

Warning in <TROOT::Append>: Replacing existing TH1: t (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: t1 (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: t2 (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: t3 (Potential memory leak).
Warning in <TROOT::Append>: Replacing existing TH1: t4 (Potential memory leak).


In [65]:
h1.Fill(1)
h1.Fill(2)

h2.Fill(1,2)
h2.Fill(2,2)

h3.Fill(3,4)
h4.Fill(5,1, 3)

30

In [119]:
canvas = draw([h1, h2], labels=['h1', 'h2'], text='pippo', min_y=0, max_y=10, h_lines=[2.], v_lines=[2], do_stats=False, y_axis_label='pipp x', x_axis_label='X')
canvas.GetRightMargin()


c_597d59 c_597d59 800 600
0 
1 same,
0 10


0.30000001192092896

In [120]:
canvas = draw([h1, h2], labels=['h1', 'h2'], text='pippo', min_y=0, max_y=10, h_lines=[2.], v_lines=[2], do_stats=False, y_axis_label='pipp x', x_axis_label='X', do_ratio=True, logy=True)
# c = canvas
# pad = c.cd(1)
# hratio.GetUpperPad().SetBottomMargin(0)
# hratio.GetUpperPad().SetRightMargin(0.3)

# pad.Update()
# pad = c.cd(2)
# hratio.GetLowerPad().SetTopMargin(0)
# hratio.GetLowerPad().SetRightMargin(0.3)
# pad.Update()
# c.Draw()
# hratio.GetLowerRefGraph().GetYaxis().SetRangeUser(-6, 6)
# c.Update()

c_61a6aa c_61a6aa 800 800
0 
1 same,
0 10


Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale


In [121]:
canvas = draw([h3, h4], labels=['h1', 'h2'], logy=True, do_profile=True, norm=True, text='pippo', max_y=9, h_lines=[2.], v_lines=[4], do_stats=False, options='COLZ', y_axis_label='pipp x')
canvas.GetRightMargin()

c_5389b6 c_5389b6 1000 500
0 COLZ
1 COLZ
0.0 9


0.12999999523162842

In [117]:
c = newCanvas(height=800, width=800)
hratio = ROOT.TRatioPlot(h1,h2)
hratio.Draw()
# hratio.GetUpperPad().SetFillColor(3)
# hratio.GetLowerPad().SetFillColor(2)

hratio.GetUpperPad().SetLogy()
hratio.GetUpperPad().Dump()

canvas.cd(3)
ROOT.gPad.SetLogy()
print ROOT.gPad.GetUymin()
print ROOT.gPad.GetUymax()

c.Draw()
# pad = c.cd(1)
hratio.SetLowTopMargin(0)
# hratio.SetUpBottomMargin(0)
# pad = c.cd(2)
# hratio.SetLowTopMargin(0)
# hratio.SetUpBottomMargin(0)


#pad = c.cd(1)




# hratio.GetUpperPad().SetBottomMargin(0)
# hratio.GetUpperPad().SetRightMargin(0.3)
# print ROOT.gPad.GetUymin()
# print ROOT.gPad.GetUymax()
# print hratio.GetUpperPad().GetUymin()
# print hratio.GetUpperPad().GetUymax()
# print hratio.GetLowerPad().GetUymin()
# print hratio.GetLowerPad().GetUymax()
# print hratio.GetLowerPad().SetFillColor(2)
# #pad.Update()
# #pad = c.cd(2)

# hratio.GetLowerPad().SetTopMargin(0)
# hratio.GetLowerPad().SetRightMargin(0.3)
# #pad.Update()
# print ROOT.gPad.GetUymin()
# print ROOT.gPad.GetUymax()

# hratio.GetLowerRefGraph().GetYaxis().SetRangeUser(-6, 6)
# c.Update()


c_8e27d2 c_8e27d2 800 800
0.0
1.0
==> Dumping object at: 0x00007fcb77e76920, name=upper_pad, class=TPad

*fTip                         ->0                 ! tool tip associated with box
fX1                           0                   X of lower X coordinate
fY1                           0                   Y of lower Y coordinate
fX2                           1                   X of upper X coordinate
fY2                           1                   Y of upper Y coordinate
fXtoAbsPixelk                 1.99005             Conversion coefficient for X World to absolute pixel
fXtoPixelk                    5e-05               Conversion coefficient for X World to pixel
fXtoPixel                     792.02              xpixel = fXtoPixelk + fXtoPixel*xworld
fYtoAbsPixelk                 540.4               Conversion coefficient for Y World to absolute pixel
fYtoPixelk                    538.47              Conversion coefficient for Y World to pixel
fYtoPixel                     -538.

Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale
Error in <THistPainter::PaintInit>: Cannot set Y axis to log scale


In [8]:
pad.Update   Double_t w = 600;
   Double_t h = 600;
   TCanvas * c1 = new TCanvas("c", "c", w, h);

SyntaxError: invalid syntax (<ipython-input-8-99b631880424>, line 1)

In [3]:
# %load ../drawingTools
import ROOT
import math
import uuid

# some useful globals, mainly to deal with ROOT idiosyncrasies
c_idx = 0
p_idx = 0
colors = range(1, 6)
stuff = []
f_idx = 0

ROOT.gStyle.SetPadBottomMargin(0.13)
ROOT.gStyle.SetPadLeftMargin(0.13)
ROOT.gStyle.SetPadRightMargin(0.30)

ROOT.gStyle.SetCanvasBorderMode(0)
ROOT.gStyle.SetCanvasColor(0)
ROOT.gStyle.SetCanvasDefH(600)
ROOT.gStyle.SetCanvasDefW(800)

# define some utility functions
def newCanvas(name=None, title=None, xdiv=0, ydiv=0, form=4):
    global c_idx
    if name is None:
        name = 'c_{}'.format(uuid.uuid4().hex[:6])
        c_idx += 1
    if title is None:
        title = name
    # print name, title
    canvas = ROOT.TCanvas(name, title)
    if(xdiv*ydiv != 0):
        canvas.Divide(xdiv, ydiv)
    global stuff
    stuff.append(canvas)
    return canvas


def draw(plot, options='', text=None):
    c = newCanvas()
    c.cd()
    plot.Draw(options)
    if text:
        rtext = getText(text, 0.15, 0.85)
        rtext.Draw('same')

    c.Draw()

    return


def drawAll(histograms,
            labels=None,
            options='',
            text=None,
            norm=False,
            logy=False,
            min_y=None,
            max_y=None,
            y_axis_label=None,
            do_ratio=False,
            do_profile=False):
    if len(histograms) == 0:
        print 'ERROR: no histogram in input'
        return -1
    if do_ratio and len(histograms) != 2:
        print 'ERROR: do_ratio option only available when 2 histograms need to be drawn!'
        return -2
    if do_profile and not ('TH2' in histograms[0].ClassName() or 'TH3' in histograms[0].ClassName()):
        print 'ERROR: do_profile option only available with TH2 and TH3 histograms'
        return -3

    # we build the canvas
    return


def drawAll(histograms,
            labels=None,
            options='',
            text=None,
            norm=False,
            logy=False,
            min_y=None,
            max_y=None,
            y_axis_label=None,
            do_ratio=False,
            do_profile=False):
    if len(histograms) == 0:
        print 'ERROR: no histogram in input'
        return -1
    if do_ratio and len(histograms) != 2:
        print 'ERROR: do_ratio option only available when 2 histograms need to be drawn!'
        return -2
    if do_profile and not ('TH2' in histograms[0].ClassName() or 'TH3' in histograms[0].ClassName()):
        print 'ERROR: do_profile option only available with TH2 and TH3 histograms'
        return -3

    # we build the canvas
    return 0


def getLegend(x1=0.7, y1=0.71, x2=0.95, y2=0.85):
    global stuff
    legend = ROOT.TLegend(x1, y1, x2, y2)
    stuff.append(legend)
    legend.SetFillColor(0)
    legend.SetFillStyle(0)
    legend.SetBorderSize(0)
    legend.SetTextSize(0.05)
    return legend


def drawAndProfileX(plot2d, miny=None, maxy=None, do_profile=True, options='', text=None):
    global p_idx
    if miny and maxy:
        plot2d.GetYaxis().SetRangeUser(miny, maxy)
    c = newCanvas()
    c.SetGrid(1, 1)
    c.cd()
    plot2d.Draw(options)
    ROOT.gPad.SetGrid(1, 1)
    ROOT.gStyle.SetGridColor(15)

    if do_profile:
        profname = plot2d.GetName()+'_prof_'+str(p_idx)
        p_idx += 1
        firstbin = 1
        lastbin = -1
        prof = plot2d.ProfileX(profname, firstbin, lastbin, 's')
        prof.SetMarkerColor(2)
        prof.SetLineColor(2)
        prof.Draw('same')

    if text:
        rtext = getText(text, 0.15, 0.85)
        rtext.Draw('same')

    c.Draw()


def getText(text, ndc_x, ndc_y):
    global stuff
    rtext = ROOT.TLatex(ndc_x, ndc_y, text)
    stuff.append(rtext)
    rtext.SetNDC(True)
    # rtext.SetTextFont(40)
    rtext.SetTextSize(0.03)
    return rtext


def drawSame(histograms,
             labels,
             options='',
             norm=False,
             logy=False,
             min_y=None,
             max_y=None,
             text=None,
             y_axis_label=None,
             x_axis_label=None,
             v_lines=None,
             h_lines=None):
    global colors
    global stuff
    c = newCanvas(title=histograms[0].GetName())
    c.cd()
    leg = getLegend()

    max_value = max_y
    min_value = min_y

    newHistos = []
    for hidx, hist in enumerate(histograms):
        hist.SetLineColor(colors[hidx])
        hist.SetStats(False)
        if norm:
            nhist = hist.DrawNormalized('same'+','+options, 1.)
            newHistos.append(nhist)
        else:
            if hidx:
                hist.Draw('same'+','+options)
            else:
                hist.Draw(options)
            newHistos.append(hist)
        leg.AddEntry(histograms[hidx], labels[hidx], 'l')

    if min_y is None:
        min_value = min([hist.GetBinContent(hist.GetMinimumBin()) for hist in newHistos])
    if max_y is None:
        max_value = max([hist.GetBinContent(hist.GetMaximumBin()) for hist in newHistos])*1.2
    print min_value, max_value

    newHistos[0].GetYaxis().SetRangeUser(min_value, max_value)
    if y_axis_label:
        newHistos[0].GetYaxis().SetTitle(y_axis_label)
    if x_axis_label:
            newHistos[0].GetXaxis().SetTitle(x_axis_label)

    leg.Draw()
    c.Draw()
    if text:
        rtext = getText(text, 0.15, 0.85)
        rtext.Draw("same")
    if logy:
        c.SetLogy()

    if v_lines:
        for v_line_x in v_lines:
            aline = ROOT.TLine(v_line_x, c.GetUymin(), v_line_x,  c.GetUymax())
            aline.SetLineStyle(2)
            aline.Draw("same")
            stuff.append(aline)
    if h_lines:
        for h_line_y in h_lines:
            aline = ROOT.TLine(c.GetUxmin(), h_line_y, c.GetUxmax(),  h_line_y)
            aline.SetLineStyle(2)
            aline.Draw("same")
            stuff.append(aline)
    c.Update()

def drawProfileX(histograms, labels, options=''):
    profiles = [hist.ProfileX() for hist in histograms]
    drawSame(profiles, labels, options)


def drawSeveral(histograms, labels, options='', do_profile=False, miny=None, maxy=None, text=None):
    ydiv = int(math.ceil(float(len(histograms))/2))
    for hidx in range(0, len(histograms)):
        newtext = labels[hidx]
        if text:
            newtext = '{}: {}'.format(labels[hidx], text)
        if do_profile:
            drawAndProfileX(histograms[hidx], miny=miny, maxy=maxy, options=options, do_profile=do_profile, text=newtext)
        else:
            draw(histograms[hidx], options=options, text=newtext)


def drawProfileRatio(prof1, prof2, ymin=None, ymax=None, text=None):
    hist1 = prof1.ProjectionX(uuid.uuid4().hex[:6])
    hist2 = prof2.ProjectionX(uuid.uuid4().hex[:6])
    hist1.Divide(hist2)
    draw(hist1)
    if text:
        rtext = getText(text, 0.15, 0.85)
        rtext.Draw("same")

    if ymin is not None and ymax is not None:
        hist1.GetYaxis().SetRangeUser(ymin, ymax)
    ROOT.gPad.Update()


# mean+-nsigmas*RMS.
def drawGaussFit(histo, nsigmas, min, max):
    minfit = histo.GetMean() - nsigmas*histo.GetRMS()
    maxfit = histo.GetMean() + nsigmas*histo.GetRMS()
    drawGFit(histo, min, max, minfit, maxfit)


# Fit a histogram in the range (minfit, maxfit) with a gaussian and
# draw it in the range (min, max)
def drawGFit(histo, min, max, minfit, maxfit):
    # static int i = 0
    # i++
    # gPad->SetGrid(1,1);
    # gStyle->SetGridColor(15);
    histo.GetXaxis().SetRangeUser(min, max)
    global f_idx
    nameF1 = "g{}".format(f_idx)
    f_idx +=1
    g1 = ROOT.TF1(nameF1, "gaus", minfit, maxfit)
    g1.SetLineColor(2)
    g1.SetLineWidth(2)
    histo.Fit(g1,"R")


def drawGraphsSame(histograms,
                   labels,
                   options='',
                   norm=False,
                   logy=False,
                   min_y=None,
                   max_y=None,
                   text=None):
    global colors
    c = newCanvas()
    c.cd()
    leg = getLegend()

    for hidx in range(0, len(histograms)):
        histograms[hidx].SetLineColor(colors[hidx])
        histograms[hidx].Draw('same'+','+options)
        leg.AddEntry(histograms[hidx], labels[hidx], 'l')

    max_value = max_y
    min_value = min_y
    if min_y is None:
        min_value = min([hist.GetBinContent(hist.GetMinimumBin()) for hist in histograms])
    if max_y is None:
        max_value = max([hist.GetBinContent(hist.GetMaximumBin()) for hist in histograms])*1.2
    histograms[0].GetYaxis().SetRangeUser(min_value, max_value)
    leg.Draw()
    c.Draw()
    if logy:
        c.SetLogy()
    if text:
        rtext = getText(text, 0.15, 0.85)
        rtext.Draw("same")
    c.Update()


In [15]:
def drawSame(histograms,
             labels,
             options='',
             norm=False,
             logy=False,
             min_y=None,
             max_y=None,
             text=None,
             y_axis_label=None,
             x_axis_label=None,
             v_lines=None,
             h_lines=None):
    global colors
    global stuff
    c = newCanvas(title=histograms[0].GetName())
    c.cd()
    leg = getLegend()
    
    max_value = max_y
    min_value = min_y
    if min_y is None:
        min_value = min([hist.GetBinContent(hist.GetMinimumBin()) for hist in histograms])
    if max_y is None:
        max_value = max([hist.GetBinContent(hist.GetMaximumBin()) for hist in histograms])*1.2

    for hidx, hist in enumerate(histograms):
        hist.SetLineColor(colors[hidx])
        if 'TH' in hist.ClassName():
            hist.SetStats(False)
        if norm:
            hist.DrawNormalized('same'+','+options, 1.)
        else:
            if hidx:
                hist.Draw('same'+','+options)
            else:
                hist.Draw(options+'PA')
        leg.AddEntry(histograms[hidx], labels[hidx], 'l')

    histograms[0].GetYaxis().SetRangeUser(min_value, max_value)
    if y_axis_label:
        histograms[0].GetYaxis().SetTitle(y_axis_label)
    if x_axis_label:
            histograms[0].GetXaxis().SetTitle(x_axis_label)

    leg.Draw()
    c.Draw()
    if text:
        rtext = getText(text, 0.15, 0.85)
        rtext.Draw("same")
    if logy:
        c.SetLogy()

    if v_lines:
        for v_line_x in v_lines:
            aline = ROOT.TLine(v_line_x, c.GetUymin(), v_line_x,  c.GetUymax())
            aline.SetLineStyle(2)
            aline.Draw("same")
            stuff.append(aline)
    if h_lines:
        for h_line_y in h_lines:
#             print h_line_y, c.GetUxmin(), c.GetUxmax()
            aline = ROOT.TLine(c.GetUxmin(), h_line_y, c.GetUxmax(),  h_line_y)
            aline.SetLineStyle(2)
            c.cd()
            aline.Draw("same")
            stuff.append(aline)
    c.Update()


In [187]:
# %load samples.py
import ROOT
import pandas as pd
import python.selections as selections

version = 'v60t'

files = {}
file_keys = {}


class RootFile:
    def __init__(self, file_name):
        global file
        self.file_name = file_name
        if self.file_name not in files.keys():
            print 'get file: {}'.format(self.file_name)
            files[self.file_name] = ROOT.TFile(self.file_name)
        self._file = files[self.file_name]
        self._file_keys = None

    def cd(self):
        self._file.cd()

    def GetListOfKeys(self):
        global file_keys
        if self.file_name not in file_keys.keys():
            print 'get list'
            file_keys[self.file_name] = self._file.GetListOfKeys()
        self._file_keys = file_keys[self.file_name]
        return self._file_keys


class Sample():
    def __init__(self, name, label, version=None, type=None):
        self.name = name
        self.label = label
        if version:
            version = '_'+version
        else:
            version = ''
        self.histo_filename = '../plots1/histos_{}{}.root'.format(self.name, version)
        self.histo_file = ROOT.TFile(self.histo_filename, 'r')
        self.type = type


# sample_names = ['ele_flat2to100_PU0',
#                 'ele_flat2to100_PU200',
#                 'photonPt35_PU0',
#                 'photonPt35_PU200']


def get_label_dict(selections):
    dictionary = {}
    for sel in selections:
        dictionary[sel.name] = sel.label
    return dictionary


class HProxy:
    def __init__(self, classtype, tp, tp_sel, gen_sel, root_file):
        self.classtype = classtype
        self.tp = tp
        self.tp_sel = tp_sel
        self.gen_sel = gen_sel
        self.root_file = root_file
        self.instance = None

    def get(self):
        if self.instance is None:
            name = '{}_{}_{}'.format(self.tp, self.tp_sel, self.gen_sel)
            if self.gen_sel is None:
                name = '{}_{}'.format(self.tp, self.tp_sel)
            self.instance = self.classtype(name, self.root_file)
        return self.instance


class HPlot:
    def __init__(self, samples, tp_sets, tp_selections, gen_selections):
        self.tp_sets = tp_sets
        self.tp_selections = tp_selections
        self.gen_selections = gen_selections
        self.pus = []
        self.labels_dict = {}

        for sample in samples:
            self.pus.append(sample.label)
            self.labels_dict[sample.type] = sample.type

        self.data = pd.DataFrame(columns=['sample', 'pu', 'tp', 'tp_sel', 'gen_sel', 'classtype', 'histo'])

        self.labels_dict.update(tp_sets)
        self.labels_dict.update(tp_selections)
        self.labels_dict.update(gen_selections)
        self.labels_dict.update({'PU0': 'PU0', 'PU200': 'PU200'})

    def cache_histo(self,
                    classtype,
                    samples,
                    pus,
                    tps,
                    tp_sels,
                    gen_sels):
        if gen_sels is None:
            gen_sels = [None]

        for sample in samples:
            print sample
            for tp in tps:
                for tp_sel in tp_sels:
                    for gen_sel in gen_sels:
                        print sample, tp, tp_sel, gen_sel
                        self.data = self.data.append({'sample': sample.type,
                                                      'pu': sample.label,
                                                      'tp': tp,
                                                      'tp_sel': tp_sel,
                                                      'gen_sel': gen_sel,
                                                      'classtype': classtype,
                                                      'histo': HProxy(classtype, tp, tp_sel, gen_sel, sample.histo_file)},
                                                     ignore_index=True)

    def get_histo(self,
                  classtype,
                  sample=None,
                  pu=None,
                  tp=None,
                  tp_sel=None,
                  gen_sel=None):
        histo = None
        labels = []
        text = ''

        query = '(pu == @pu) & (tp == @tp) & (tp_sel == @tp_sel) & (classtype == @classtype)'
        if gen_sel is not None:
            query += ' & (gen_sel == @gen_sel)'
        else:
            query += ' & (gen_sel.isnull())'
        if sample is not None:
            query += '& (sample == @sample)'

        histo_df = self.data.query(query)

        if histo_df.empty:
            print 'No match found for: pu: {}, tp: {}, tp_sel: {}, gen_sel: {}, classtype: {}'.format(pu, tp, tp_sel, gen_sel, classtype)
            return None, None, None
#         print histo_df

        field_counts = histo_df.apply(lambda x: len(x.unique()))
        label_fields = []
        text_fields = []
        # print field_counts
        for field in field_counts.iteritems():
            if(field[1] > 1 and field[0] != 'histo'):
                label_fields.append(field[0])
            if(field[1] == 1 and field[0] != 'histo' and field[0] != 'classtype' and field[0] != 'sample'):
                if(gen_sel is None and field[0] == 'gen_sel'):
                    continue
                text_fields.append(field[0])
#         print 'label fields: {}'.format(label_fields)
#         print 'text fields: {}'.format(text_fields)

        for item in histo_df[label_fields].iterrows():
            labels.append(', '.join([self.labels_dict[tx] for tx in item[1].values if self.labels_dict[tx] != '']))

        # print labels
        text = ', '.join([self.labels_dict[fl] for fl in histo_df[text_fields].iloc[0].values if self.labels_dict[fl] != ''])
        histo = [his.get() for his in histo_df['histo'].values]
        return histo, labels, text


# -------------------------------------------------------------------------

samples_ele = [
    Sample('ele_flat2to100_PU0', 'PU0', version, 'ele'),
    Sample('ele_flat2to100_PU200', 'PU200', version, 'ele')
    ]

samples_photons = [
    Sample('photon_flat8to150_PU0', 'PU0', version, 'photon'),
    Sample('photon_flat8to150_PU200', 'PU200', version, 'photon')
    ]

samples_pions = [
    Sample('pion_flat2to100_PU0', 'PU0', version, 'pions'),
    ]

samples_nugus = [
    Sample('nugun_alleta_pu0', 'PU0', version, 'mb'),
    Sample('nugun_alleta_pu200', 'PU200', version, 'mb')
    ]

samples_nugunrates = [
    Sample('nugun_alleta_pu200', 'PU200', version, 'mb')
    ]

tpsets = {'DEF': 'NNDR',
          'DEFCalib': 'NNDR Calib v1',
          'DEFMerged': 'NNDR(merged)'}

tpset_selections = {}
gen_selections = {}
samples = []

# tpset_selections.update(get_label_dict(tp_rate_selections))
tpset_selections.update(get_label_dict(selections.tp_match_selections))
gen_selections.update(get_label_dict(selections.gen_part_selections))
gen_selections.update({'nomatch': ''})


gen_part_selections: 10


Error in <TFile::TFile>: file ../plots1/histos_photon_flat8to150_PU0_v60t.root does not exist
Error in <TFile::TFile>: file ../plots1/histos_photon_flat8to150_PU200_v60t.root does not exist
Error in <TFile::TFile>: file ../plots1/histos_pion_flat2to100_PU0_v60t.root does not exist
Error in <TFile::TFile>: file ../plots1/histos_nugun_alleta_pu0_v60t.root does not exist
Error in <TFile::TFile>: file ../plots1/histos_nugun_alleta_pu200_v60t.root does not exist
Error in <TFile::TFile>: file ../plots1/histos_nugun_alleta_pu200_v60t.root does not exist


In [188]:
%%time
# for key in samples_ele[0].histo_file.GetListOfKeys():
#     #pass
#     key.GetName()
# print len(samples_ele[0].histo_file.GetListOfKeys())
# l = [histo for histo in samples_ele[0].histo_file.GetListOfKeys()]
l = [(histo.ReadObj(), histo.GetName()) for histo in samples_ele[0].histo_file.GetListOfKeys() if 'DEF_all'+'_' in histo.GetName()]

CPU times: user 9.13 ms, sys: 6.18 ms, total: 15.3 ms
Wall time: 24.8 ms


In [189]:
%%time

hplot = HPlot(samples, tpsets, tpset_selections, gen_selections)
samples = samples_ele


hplot.cache_histo(classtype=histos.HistoSetEff, 
                  samples=samples,
                  pus=[],
                  tps=tpsets,
                  tp_sels=tpset_selections,
                  gen_sels=gen_selections)



<__main__.Sample instance at 0x123c05d40>
<__main__.Sample instance at 0x123c05d40> DEFMerged Em GENPt40
<__main__.Sample instance at 0x123c05d40> DEFMerged Em GENEtaC
<__main__.Sample instance at 0x123c05d40> DEFMerged Em GENEtaB
<__main__.Sample instance at 0x123c05d40> DEFMerged Em GENEtaD
<__main__.Sample instance at 0x123c05d40> DEFMerged Em GENEtaBC
<__main__.Sample instance at 0x123c05d40> DEFMerged Em GENPt30
<__main__.Sample instance at 0x123c05d40> DEFMerged Em GENPt20
<__main__.Sample instance at 0x123c05d40> DEFMerged Em GENEtaBCD
<__main__.Sample instance at 0x123c05d40> DEFMerged Em GENPt10
<__main__.Sample instance at 0x123c05d40> DEFMerged Em nomatch
<__main__.Sample instance at 0x123c05d40> DEFMerged Em GEN
<__main__.Sample instance at 0x123c05d40> DEFMerged all GENPt40
<__main__.Sample instance at 0x123c05d40> DEFMerged all GENEtaC
<__main__.Sample instance at 0x123c05d40> DEFMerged all GENEtaB
<__main__.Sample instance at 0x123c05d40> DEFMerged all GENEtaD
<__main__.

<__main__.Sample instance at 0x123c05d40> DEFCalib Em GENEtaC
<__main__.Sample instance at 0x123c05d40> DEFCalib Em GENEtaB
<__main__.Sample instance at 0x123c05d40> DEFCalib Em GENEtaD
<__main__.Sample instance at 0x123c05d40> DEFCalib Em GENEtaBC
<__main__.Sample instance at 0x123c05d40> DEFCalib Em GENPt30
<__main__.Sample instance at 0x123c05d40> DEFCalib Em GENPt20
<__main__.Sample instance at 0x123c05d40> DEFCalib Em GENEtaBCD
<__main__.Sample instance at 0x123c05d40> DEFCalib Em GENPt10
<__main__.Sample instance at 0x123c05d40> DEFCalib Em nomatch
<__main__.Sample instance at 0x123c05d40> DEFCalib Em GEN
<__main__.Sample instance at 0x123c05d40> DEFCalib all GENPt40
<__main__.Sample instance at 0x123c05d40> DEFCalib all GENEtaC
<__main__.Sample instance at 0x123c05d40> DEFCalib all GENEtaB
<__main__.Sample instance at 0x123c05d40> DEFCalib all GENEtaD
<__main__.Sample instance at 0x123c05d40> DEFCalib all GENEtaBC
<__main__.Sample instance at 0x123c05d40> DEFCalib all GENPt30
<_

<__main__.Sample instance at 0x123c05d40> DEF Em GEN
<__main__.Sample instance at 0x123c05d40> DEF all GENPt40
<__main__.Sample instance at 0x123c05d40> DEF all GENEtaC
<__main__.Sample instance at 0x123c05d40> DEF all GENEtaB
<__main__.Sample instance at 0x123c05d40> DEF all GENEtaD
<__main__.Sample instance at 0x123c05d40> DEF all GENEtaBC
<__main__.Sample instance at 0x123c05d40> DEF all GENPt30
<__main__.Sample instance at 0x123c05d40> DEF all GENPt20
<__main__.Sample instance at 0x123c05d40> DEF all GENEtaBCD
<__main__.Sample instance at 0x123c05d40> DEF all GENPt10
<__main__.Sample instance at 0x123c05d40> DEF all nomatch
<__main__.Sample instance at 0x123c05d40> DEF all GEN
<__main__.Sample instance at 0x123c05d40> DEF Pt10 GENPt40
<__main__.Sample instance at 0x123c05d40> DEF Pt10 GENEtaC
<__main__.Sample instance at 0x123c05d40> DEF Pt10 GENEtaB
<__main__.Sample instance at 0x123c05d40> DEF Pt10 GENEtaD
<__main__.Sample instance at 0x123c05d40> DEF Pt10 GENEtaBC
<__main__.Samp

<__main__.Sample instance at 0x123c218c0> DEFMerged Pt10 GEN
<__main__.Sample instance at 0x123c218c0> DEFMerged Emv1Pt30 GENPt40
<__main__.Sample instance at 0x123c218c0> DEFMerged Emv1Pt30 GENEtaC
<__main__.Sample instance at 0x123c218c0> DEFMerged Emv1Pt30 GENEtaB
<__main__.Sample instance at 0x123c218c0> DEFMerged Emv1Pt30 GENEtaD
<__main__.Sample instance at 0x123c218c0> DEFMerged Emv1Pt30 GENEtaBC
<__main__.Sample instance at 0x123c218c0> DEFMerged Emv1Pt30 GENPt30
<__main__.Sample instance at 0x123c218c0> DEFMerged Emv1Pt30 GENPt20
<__main__.Sample instance at 0x123c218c0> DEFMerged Emv1Pt30 GENEtaBCD
<__main__.Sample instance at 0x123c218c0> DEFMerged Emv1Pt30 GENPt10
<__main__.Sample instance at 0x123c218c0> DEFMerged Emv1Pt30 nomatch
<__main__.Sample instance at 0x123c218c0> DEFMerged Emv1Pt30 GEN
<__main__.Sample instance at 0x123c218c0> DEFMerged EmPt30 GENPt40
<__main__.Sample instance at 0x123c218c0> DEFMerged EmPt30 GENEtaC
<__main__.Sample instance at 0x123c218c0> DEFMe

<__main__.Sample instance at 0x123c218c0> DEFCalib EmPt30 GEN
<__main__.Sample instance at 0x123c218c0> DEFCalib EmPt20 GENPt40
<__main__.Sample instance at 0x123c218c0> DEFCalib EmPt20 GENEtaC
<__main__.Sample instance at 0x123c218c0> DEFCalib EmPt20 GENEtaB
<__main__.Sample instance at 0x123c218c0> DEFCalib EmPt20 GENEtaD
<__main__.Sample instance at 0x123c218c0> DEFCalib EmPt20 GENEtaBC
<__main__.Sample instance at 0x123c218c0> DEFCalib EmPt20 GENPt30
<__main__.Sample instance at 0x123c218c0> DEFCalib EmPt20 GENPt20
<__main__.Sample instance at 0x123c218c0> DEFCalib EmPt20 GENEtaBCD
<__main__.Sample instance at 0x123c218c0> DEFCalib EmPt20 GENPt10
<__main__.Sample instance at 0x123c218c0> DEFCalib EmPt20 nomatch
<__main__.Sample instance at 0x123c218c0> DEFCalib EmPt20 GEN
<__main__.Sample instance at 0x123c218c0> DEFCalib Emv1Pt20 GENPt40
<__main__.Sample instance at 0x123c218c0> DEFCalib Emv1Pt20 GENEtaC
<__main__.Sample instance at 0x123c218c0> DEFCalib Emv1Pt20 GENEtaB
<__main__

<__main__.Sample instance at 0x123c218c0> DEF EmPt20 GENEtaD
<__main__.Sample instance at 0x123c218c0> DEF EmPt20 GENEtaBC
<__main__.Sample instance at 0x123c218c0> DEF EmPt20 GENPt30
<__main__.Sample instance at 0x123c218c0> DEF EmPt20 GENPt20
<__main__.Sample instance at 0x123c218c0> DEF EmPt20 GENEtaBCD
<__main__.Sample instance at 0x123c218c0> DEF EmPt20 GENPt10
<__main__.Sample instance at 0x123c218c0> DEF EmPt20 nomatch
<__main__.Sample instance at 0x123c218c0> DEF EmPt20 GEN
<__main__.Sample instance at 0x123c218c0> DEF Emv1Pt20 GENPt40
<__main__.Sample instance at 0x123c218c0> DEF Emv1Pt20 GENEtaC
<__main__.Sample instance at 0x123c218c0> DEF Emv1Pt20 GENEtaB
<__main__.Sample instance at 0x123c218c0> DEF Emv1Pt20 GENEtaD
<__main__.Sample instance at 0x123c218c0> DEF Emv1Pt20 GENEtaBC
<__main__.Sample instance at 0x123c218c0> DEF Emv1Pt20 GENPt30
<__main__.Sample instance at 0x123c218c0> DEF Emv1Pt20 GENPt20
<__main__.Sample instance at 0x123c218c0> DEF Emv1Pt20 GENEtaBCD
<__mai

In [190]:
%%time

for pu in ['PU0', 'PU200']:
    for tp in tpsets:
        for tp_sel in tpset_selections:
            tp_sel_den = 'all'
            if 'Pt' in tp_sel:
                # print tp_sel
                tp_sel_den = tp_sel.split('Pt')[0]
                if tp_sel_den == '':
                    tp_sel_den = 'all'
                print '{} den -> {}'.format(tp_sel, tp_sel_den) 
            else:
                continue
            for gen_sel in ['GEN', 'GENEtaB', 'GENEtaBC', 'GENEtaBCD', 'GENEtaC', 'GENEtaD']:
                hsetden = hplot.get_histo(histos.HistoSetEff, 'ele', pu, tp, tp_sel_den, gen_sel)
                hset = hplot.get_histo(histos.HistoSetEff, 'ele', pu, tp, tp_sel, gen_sel)
#                 print hset[0][0].name
#                 print hsetden[0][0].name
                hset[0][0].computeTurnOn(hsetden[0][0].h_num)


Pt10 den -> all
Emv1Pt30 den -> Emv1
EmPt30 den -> Em
EmPt20 den -> Em
Emv1Pt20 den -> Emv1
Pt30 den -> all
Pt20 den -> all
EmPt10 den -> Em
Emv1Pt10 den -> Emv1
Pt10 den -> all
Emv1Pt30 den -> Emv1
EmPt30 den -> Em
EmPt20 den -> Em
Emv1Pt20 den -> Emv1
Pt30 den -> all
Pt20 den -> all
EmPt10 den -> Em
Emv1Pt10 den -> Emv1
Pt10 den -> all
Emv1Pt30 den -> Emv1
EmPt30 den -> Em
EmPt20 den -> Em
Emv1Pt20 den -> Emv1
Pt30 den -> all
Pt20 den -> all
EmPt10 den -> Em
Emv1Pt10 den -> Emv1
Pt10 den -> all
Emv1Pt30 den -> Emv1
EmPt30 den -> Em
EmPt20 den -> Em
Emv1Pt20 den -> Emv1
Pt30 den -> all
Pt20 den -> all
EmPt10 den -> Em
Emv1Pt10 den -> Emv1
Pt10 den -> all
Emv1Pt30 den -> Emv1
EmPt30 den -> Em
EmPt20 den -> Em
Emv1Pt20 den -> Emv1
Pt30 den -> all
Pt20 den -> all
EmPt10 den -> Em
Emv1Pt10 den -> Emv1
Pt10 den -> all
Emv1Pt30 den -> Emv1
EmPt30 den -> Em
EmPt20 den -> Em
Emv1Pt20 den -> Emv1
Pt30 den -> all
Pt20 den -> all
EmPt10 den -> Em
Emv1Pt10 den -> Emv1
CPU times: user 37.3 s, sys:

In [191]:
hplot.data

sample     pu         tp    tp_sel    gen_sel  \
0      ele    PU0  DEFMerged        Em    GENPt40   
1      ele    PU0  DEFMerged        Em    GENEtaC   
2      ele    PU0  DEFMerged        Em    GENEtaB   
3      ele    PU0  DEFMerged        Em    GENEtaD   
4      ele    PU0  DEFMerged        Em   GENEtaBC   
5      ele    PU0  DEFMerged        Em    GENPt30   
6      ele    PU0  DEFMerged        Em    GENPt20   
7      ele    PU0  DEFMerged        Em  GENEtaBCD   
8      ele    PU0  DEFMerged        Em    GENPt10   
9      ele    PU0  DEFMerged        Em    nomatch   
10     ele    PU0  DEFMerged        Em        GEN   
11     ele    PU0  DEFMerged       all    GENPt40   
12     ele    PU0  DEFMerged       all    GENEtaC   
13     ele    PU0  DEFMerged       all    GENEtaB   
14     ele    PU0  DEFMerged       all    GENEtaD   
15     ele    PU0  DEFMerged       all   GENEtaBC   
16     ele    PU0  DEFMerged       all    GENPt30   
17     ele    PU0  DEFMerged       all    GENPt20   
18     ele    PU0  DEFMerged       all  GENEtaBCD   
19     ele    PU0  DEFMerged       all    GENPt10   
20     ele    PU0  DEFMerged       all    nomatch   
21     ele    PU0  DEFMerged       all        GEN   
22     ele    PU0  DEFMerged      Pt10    GENPt40   
23     ele    PU0  DEFMerged      Pt10    GENEtaC   
24     ele    PU0  DEFMerged      Pt10    GENEtaB   
25     ele    PU0  DEFMerged      Pt10    GENEtaD   
26     ele    PU0  DEFMerged      Pt10   GENEtaBC   
27     ele    PU0  DEFMerged      Pt10    GENPt30   
28     ele    PU0  DEFMerged      Pt10    GENPt20   
29     ele    PU0  DEFMerged      Pt10  GENEtaBCD   
..     ...    ...        ...       ...        ...   
762    ele  PU200        DEF    EmPt10    GENEtaD   
763    ele  PU200        DEF    EmPt10   GENEtaBC   
764    ele  PU200        DEF    EmPt10    GENPt30   
765    ele  PU200        DEF    EmPt10    GENPt20   
766    ele  PU200        DEF    EmPt10  GENEtaBCD   
767    ele  PU200        DEF    EmPt10    GENPt10   
768    ele  PU200        DEF    EmPt10    nomatch   
769    ele  PU200        DEF    EmPt10        GEN   
770    ele  PU200        DEF  Emv1Pt10    GENPt40   
771    ele  PU200        DEF  Emv1Pt10    GENEtaC   
772    ele  PU200        DEF  Emv1Pt10    GENEtaB   
773    ele  PU200        DEF  Emv1Pt10    GENEtaD   
774    ele  PU200        DEF  Emv1Pt10   GENEtaBC   
775    ele  PU200        DEF  Emv1Pt10    GENPt30   
776    ele  PU200        DEF  Emv1Pt10    GENPt20   
777    ele  PU200        DEF  Emv1Pt10  GENEtaBCD   
778    ele  PU200        DEF  Emv1Pt10    GENPt10   
779    ele  PU200        DEF  Emv1Pt10    nomatch   
780    ele  PU200        DEF  Emv1Pt10        GEN   
781    ele  PU200        DEF      Emv1    GENPt40   
782    ele  PU200        DEF      Emv1    GENEtaC   
783    ele  PU200        DEF      Emv1    GENEtaB   
784    ele  PU200        DEF      Emv1    GENEtaD   
785    ele  PU200        DEF      Emv1   GENEtaBC   
786    ele  PU200        DEF      Emv1    GENPt30   
787    ele  PU200        DEF      Emv1    GENPt20   
788    ele  PU200        DEF      Emv1  GENEtaBCD   
789    ele  PU200        DEF      Emv1    GENPt10   
790    ele  PU200        DEF      Emv1    nomatch   
791    ele  PU200        DEF      Emv1        GEN   

                        classtype                                      histo  
0    python.l1THistos.HistoSetEff  <__main__.HProxy instance at 0x123c32368>  
1    python.l1THistos.HistoSetEff  <__main__.HProxy instance at 0x123c324d0>  
2    python.l1THistos.HistoSetEff  <__main__.HProxy instance at 0x122bf5d40>  
3    python.l1THistos.HistoSetEff  <__main__.HProxy instance at 0x122b0c050>  
4    python.l1THistos.HistoSetEff  <__main__.HProxy instance at 0x123c32248>  
5    python.l1THistos.HistoSetEff  <__main__.HProxy instance at 0x122a859e0>  
6    python.l1THistos.HistoSetEff  <__main__.HProxy instance at 0x122c07248>  
7    python.l1THistos.HistoSetEff  <__main__.HProxy instance at 0x122b0ca70>  
8    p

In [193]:
tps = ['DEF', 'DEFCalib','DEFMerged']
tp_select = ['all', 'Em' ,'Emv1']
gen_select = ['GEN', 'GENEtaB', 'GENEtaC', 'GENEtaD', 
              'GENEtaBC', 'GENEtaBCD' ]


## Effinciency vs $\eta$

In [13]:
line_m1p52 = ROOT.TLine(-1.52,0, -1.52, 1.1)
line_m1p52.SetLineStyle(2)
line_p1p52 = ROOT.TLine(1.52,0, 1.52, 1.1)
line_p1p52.SetLineStyle(2)
line_m1p7 = ROOT.TLine(-1.7,0, -1.7, 1.1)
line_m1p7.SetLineStyle(2)
line_p1p7 = ROOT.TLine(1.7,0, 1.7, 1.1)
line_p1p7.SetLineStyle(2)
line_m2p8 = ROOT.TLine(-2.8,0, -2.8, 1.1)
line_m2p8.SetLineStyle(2)
line_p2p8 = ROOT.TLine(2.8,0, 2.8, 1.1)
line_p2p8.SetLineStyle(2)

In [228]:
for tp in tps:
    for tp_sel in tp_select:
        for gen_sel in ['GEN']:
            hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)
            # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
            draw([his.h_eff.h_eta.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, v_lines=[-2.8, -2.4, -1.7, -1.52, 1.52, 1.7, 2.4, 2.8])
#             print [his.h_num.h_eta.GetName() for his in hsets]

c_93c42f c_93c42f 800 600
0 PA
1 same,
0 1.1
c_eb5c1b c_eb5c1b 800 600
0 PA
1 same,
0 1.1
c_cb7cce c_cb7cce 800 600
0 PA
1 same,
0 1.1
c_1fa826 c_1fa826 800 600
0 PA
1 same,
0 1.1
c_ac27ec c_ac27ec 800 600
0 PA
1 same,
0 1.1
c_48def5 c_48def5 800 600
0 PA
1 same,
0 1.1
c_962585 c_962585 800 600
0 PA
1 same,
0 1.1
c_90c048 c_90c048 800 600
0 PA
1 same,
0 1.1
c_0acae8 c_0acae8 800 600
0 PA
1 same,
0 1.1


In [230]:
for tp in tps:
    for tp_sel in ['EmPt20', 'Emv1Pt20']:
        for gen_sel in ['GENPt30']:
            hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)
            # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
            draw([his.h_eff.h_eta.CreateGraph() for his in hsets], labels, 
                     text=text, min_y=0, max_y=1.1, 
                     v_lines=[-2.8, -2.4, -1.7, -1.52, 1.52, 1.7, 2.4, 2.8],
                     y_axis_label='(L1>thr. & matched to GEN)/GEN',
                     options='P')
     

c_944dbd c_944dbd 800 600
0 PPA
1 same,P
0 1.1
c_a9ff04 c_a9ff04 800 600
0 PPA
1 same,P
0 1.1
c_b25ffd c_b25ffd 800 600
0 PPA
1 same,P
0 1.1
c_ad1855 c_ad1855 800 600
0 PPA
1 same,P
0 1.1
c_fce5d1 c_fce5d1 800 600
0 PPA
1 same,P
0 1.1
c_e5a3e4 c_e5a3e4 800 600
0 PPA
1 same,P
0 1.1


In [231]:
for pu in ['PU0', 'PU200']:
    for tp_sel in ['EmPt20', 'Emv1Pt20']:
        for gen_sel in ['GENPt30']:
            hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, ['DEF', 'DEFCalib'], tp_sel, gen_sel)
            # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
            draw([his.h_eff.h_eta.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, v_lines=[-2.8, -2.4, -1.7, -1.52, 1.52, 1.7, 2.4, 2.8])
   

c_42736f c_42736f 800 600
0 PA
1 same,
0 1.1
c_25929d c_25929d 800 600
0 PA
1 same,
0 1.1
c_4d5c22 c_4d5c22 800 600
0 PA
1 same,
0 1.1
c_74bdc9 c_74bdc9 800 600
0 PA
1 same,
0 1.1


In [232]:
for pu in ['PU0', 'PU200']:
    for tp_sel in ['Pt20', 'EmPt20', 'Emv1Pt20']:
        for gen_sel in ['GENPt30']:
            hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, ['DEF', 'DEFMerged'], tp_sel, gen_sel)
            # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
            draw([his.h_eff.h_eta.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, v_lines=[-2.8, -2.4, -1.7, -1.52, 1.52, 1.7, 2.4, 2.8])
   

c_d9ba1c c_d9ba1c 800 600
0 PA
1 same,
0 1.1
c_c8a16f c_c8a16f 800 600
0 PA
1 same,
0 1.1
c_116eef c_116eef 800 600
0 PA
1 same,
0 1.1
c_3a1039 c_3a1039 800 600
0 PA
1 same,
0 1.1
c_9b39db c_9b39db 800 600
0 PA
1 same,
0 1.1
c_ceb7c3 c_ceb7c3 800 600
0 PA
1 same,
0 1.1


#### Old vs New EGID: eff vs $\eta$

In [233]:
for pu in ['PU0', 'PU200']:
    for gen_sel in ['GENPt30']:
        hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, ['DEF'], ['EmPt20', 'Emv1Pt20'], gen_sel)
        # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
        draw([his.h_eff.h_eta.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, v_lines=[-2.8, -2.4, -1.7, -1.52, 1.52, 1.7, 2.4, 2.8])
   

c_8e6647 c_8e6647 800 600
0 PA
1 same,
0 1.1
c_0c1ac6 c_0c1ac6 800 600
0 PA
1 same,
0 1.1


## Efficiency vs $p_{T}$

In [14]:
line_y1p0 = ROOT.TLine(0.,1., 110., 1.)
line_y0p95 = ROOT.TLine(0.,0.95, 110., 0.95)
line_y0p95.SetLineStyle(2)

In [234]:
for tp in tps:
    for tp_sel in ['all', 'Em', 'Emv1']:
        for gen_sel in gen_select:
            hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)
            # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
            draw([his.h_eff.h_pt.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, y_axis_label='L1 matched to GEN/GEN', h_lines=[0.95, 1] )


c_ef2124 c_ef2124 800 600
0 PA
1 same,
0 1.1
c_6f7188 c_6f7188 800 600
0 PA
1 same,
0 1.1
c_207f3e c_207f3e 800 600
0 PA
1 same,
0 1.1
c_ceb727 c_ceb727 800 600
0 PA
1 same,
0 1.1
c_e05807 c_e05807 800 600
0 PA
1 same,
0 1.1
c_e8de61 c_e8de61 800 600
0 PA
1 same,
0 1.1
c_deacd3 c_deacd3 800 600
0 PA
1 same,
0 1.1
c_0d9e8e c_0d9e8e 800 600
0 PA
1 same,
0 1.1
c_a1bfd6 c_a1bfd6 800 600
0 PA
1 same,
0 1.1
c_870516 c_870516 800 600
0 PA
1 same,
0 1.1
c_5a99d9 c_5a99d9 800 600
0 PA
1 same,
0 1.1
c_6655f4 c_6655f4 800 600
0 PA
1 same,
0 1.1
c_ca57c0 c_ca57c0 800 600
0 PA
1 same,
0 1.1
c_72a0a2 c_72a0a2 800 600
0 PA
1 same,
0 1.1
c_e6fe8f c_e6fe8f 800 600
0 PA
1 same,
0 1.1
c_f78e5b c_f78e5b 800 600
0 PA
1 same,
0 1.1
c_073e7f c_073e7f 800 600
0 PA
1 same,
0 1.1
c_48d21c c_48d21c 800 600
0 PA
1 same,
0 1.1
c_4ccf60 c_4ccf60 800 600
0 PA
1 same,
0 1.1
c_7b7e2d c_7b7e2d 800 600
0 PA
1 same,
0 1.1
c_0e6767 c_0e6767 800 600
0 PA
1 same,
0 1.1
c_98a0c7 c_98a0c7 800 600
0 PA
1 same,
0 1.1
c_f60f7b c

#### OLD VS NEW EGID VS $p_{T}$

In [235]:
for pu in ['PU0', 'PU200']:
    for tp in ['DEF']:
        for gen_sel in gen_select:
            hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, tp, ['all', 'Em', 'Emv1'], gen_sel)
            # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
            draw([his.h_eff.h_pt.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, y_axis_label='L1 matched to GEN/GEN', h_lines=[0.95, 1])


c_50047f c_50047f 800 600
0 PA
1 same,
2 same,
0 1.1
c_e3e96d c_e3e96d 800 600
0 PA
1 same,
2 same,
0 1.1
c_b52a37 c_b52a37 800 600
0 PA
1 same,
2 same,
0 1.1
c_cd3a38 c_cd3a38 800 600
0 PA
1 same,
2 same,
0 1.1
c_638451 c_638451 800 600
0 PA
1 same,
2 same,
0 1.1
c_c44d03 c_c44d03 800 600
0 PA
1 same,
2 same,
0 1.1
c_76388f c_76388f 800 600
0 PA
1 same,
2 same,
0 1.1
c_b9a3ae c_b9a3ae 800 600
0 PA
1 same,
2 same,
0 1.1
c_2b80f2 c_2b80f2 800 600
0 PA
1 same,
2 same,
0 1.1
c_5f5cbc c_5f5cbc 800 600
0 PA
1 same,
2 same,
0 1.1
c_a2a881 c_a2a881 800 600
0 PA
1 same,
2 same,
0 1.1
c_815889 c_815889 800 600
0 PA
1 same,
2 same,
0 1.1


In [25]:
for pu in ['PU0', 'PU200']:
    for tp_sel in ['Em']:
        for gen_sel in gen_select:
            hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, ['DEF', 'DEFMerged'], tp_sel, gen_sel)
            # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
            drawSame([his.h_eff.h_pt.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, y_axis_label='L1 matched to GEN/GEN', h_lines=[0.95, 1])


## Turn-on curves

In [26]:
for tp in tps:
    for tp_sel in ['Pt20', 'EmPt20', 'Emv1Pt20', 'Pt30', 'EmPt30', 'Emv1Pt30']:
        for gen_sel in gen_select:
            hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', ['PU0', 'PU200'], tp, tp_sel, gen_sel)
            # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
            drawSame([his.h_ton.h_pt.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, y_axis_label='L1 matched to GEN and p_{T}>th./L1 matched to GEN', h_lines=[0.95, 1])
   

In [27]:
for pu in ['PU0', 'PU200']:
    for tp in tps:
        for tp_sel in ['Pt20', 'EmPt20', 'Emv1Pt20', 'Pt30', 'EmPt30', 'Emv1Pt30']:
                hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, tp, tp_sel, ['GENEtaABC', 'GENEtaBC'])
                # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
                drawSame([his.h_ton.h_pt.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, y_axis_label='L1 matched to GEN and p_{T}>th./L1 matched to GEN', h_lines=[0.95, 1])
   

In [28]:
for pu in ['PU0', 'PU200']:
        for tp_sel in ['EmPt20', 'Emv1Pt20', 'EmPt30', 'Emv1Pt30']:
            for gen_sel in gen_select:
                hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, ['DEF', 'DEFCalib'], tp_sel, gen_sel)
                # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
                drawSame([his.h_ton.h_pt.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, y_axis_label='L1 matched to GEN and p_{T}>th./L1 matched to GEN', h_lines=[0.95, 1])
   

In [229]:
for pu in ['PU0', 'PU200']:
        for tp_sel in ['EmPt20', 'Emv1Pt20', 'EmPt30', 'Emv1Pt30']:
            hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, ['DEF', 'DEFCalib'], tp_sel, ['GENEtaABC', 'GENEtaBC'])
            # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
            draw([his.h_ton.h_pt.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, y_axis_label='L1 matched to GEN and p_{T}>th./L1 matched to GEN', h_lines=[0.95, 1])
   

c_09dc97 c_09dc97 800 600
0 PA
1 same,
0 1.1
c_da7e19 c_da7e19 800 600
0 PA
1 same,
0 1.1
c_52a47f c_52a47f 800 600
0 PA
1 same,
0 1.1
c_9a3922 c_9a3922 800 600
0 PA
1 same,
0 1.1
c_72e9a5 c_72e9a5 800 600
0 PA
1 same,
0 1.1
c_e0d5e6 c_e0d5e6 800 600
0 PA
1 same,
0 1.1
c_1fe2b5 c_1fe2b5 800 600
0 PA
1 same,
0 1.1
c_cd05cd c_cd05cd 800 600
0 PA
1 same,
0 1.1


In [29]:
for pu in ['PU0', 'PU200']:
        for tp_sel in ['EmPt20', 'Emv1Pt20', 'EmPt30', 'Emv1Pt30']:
            for gen_sel in gen_select:
                hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, ['DEF', 'DEFMerged'], tp_sel, gen_sel)
                # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
                drawSame([his.h_ton.h_pt.CreateGraph() for his in hsets], labels, text=text, min_y=0, max_y=1.1, y_axis_label='L1 matched to GEN and p_{T}>th./L1 matched to GEN', h_lines=[0.95, 1])
   

## Scaling

In [30]:
def f_yc(x, par):
    return (ROOT.Math.normal_cdf(par[0]*(x[0]-par[1]), par[0]*par[2], 0) - ROOT.TMath.Exp(-par[0]*(x[0]-par[1])+par[0]*par[0]*par[2]*par[2]/2)*ROOT.Math.normal_cdf(par[0]*(x[0]-par[1]), par[0]*par[2], par[0]*par[0]*par[2]*par[2])) * (par[3] - par[4]) + par[4]

tf_yc = ROOT.TF1('tf_yc', f_yc, 0, 100, 5)
tf_yc.SetParameters(1, 20, 4, 1.0, 0.0);
tf_yc.SetParNames("#lambda", "#mu", "#sigma", "Plateau", "Baseline");
tf_yc.SetLineColor(6)
tf_yc.FixParameter(4,0)

tf_yc.SetParLimits(3, 0.8, 1)
tf_yc.SetParLimits(0, 0, 1)

c = newCanvas()
tf_yc.Draw()
c.Draw()


In [34]:

import numpy as np
from array import array

def f_cb(x, par):
    return ROOT.Math.crystalball_function(x[0], par[0], par[1], par[2], par[3])

tf_cb = ROOT.TF1('cb', f_cb, 0, 100, 4)
tf_cb.SetParameters(10., 4., 3, 20.)

def f_cbi(x, par):
    return ROOT.Math.crystalball_cdf(x[0], par[0], par[1], par[2], par[3])
#     tf_cb.SetParameters(par[0], par[1], par[2], par[3])
#     npts = 1000
#     x_ = []
#     w_ = []
   
#     return tf_cb.IntegralFast(npts, np.array(npts), np.array(npts), 0., x[0])
    #return tf_cb.Integral(0., x[0])
    
    
tf_cbi = ROOT.TF1('cbi', f_cbi, 0, 100, 4)
tf_cbi.SetParameters(10., 4., 3, 20.)
tf_cbi.SetLineColor(4)

c = newCanvas()
tf_cbi.Draw()
c.Draw()


    # ROOT::Math::crystalball_function (double x, double alpha, double n, double sigma, double x0=0)

# fitf_cb = ROOT.TF1('cbfunc', 'ROOT.TMath.crystalball_function (x, [0], [1], [2], [3])', 0, 100)
# 

# fitf_cb.SetParameters(1, 1, 1, 0)


In [37]:
# Double_t turnon_func(Double_t *x, Double_t *par)
# {
#   double halfpoint = par[0];
#   double slope = par[1];
#   double plateau = par[2];

#   //double offset = par[3];
#   //double plateau = 1.0;
#   double offset = 0;

#   double pt = TMath::Max(x[0],0.000001);

#    double arg = 0;
#    //cout << pt <<", "<< halfpoint <<", " << slope <<endl;
#    arg = (pt - halfpoint)/(TMath::Sqrt(pt)*slope);
#    double fitval = offset+0.5*plateau*(1+TMath::Erf(arg));
#    return fitval;
# }




def turnon_func1(x, par):

    return 0.5 * par[0] * (1+ROOT.TMath.Erf((x[0]-par[1])/(par[2]*ROOT.TMath.Sqrt(2))))




def turnon_func(x, par):
  
    halfpoint = par[0]
    slope = par[1]
    plateau = par[2]
    offset = 0
    pt = ROOT.TMath.Max(x[0],0.000001)
    arg = 0
    arg = (pt - halfpoint)/(ROOT.TMath.Sqrt(pt)*slope)
    fitval = offset+0.5*plateau*(1+ROOT.TMath.Erf(arg))
    return fitval

fitf_to = ROOT.TF1('myfunc', turnon_func1, 0, 100, 3)
#fitf.SetParNames('#epsilon', "#mu", '#sigma')
fitf_to.SetParameters(1,25,2)
fitf_to.SetLineColor(3)

def fermi(x, params):
    return params[3]*(params[0] - 1/(ROOT.TMath.Exp((x[0]-params[1])/(params[2]))+1))
  
fitf = ROOT.TF1('myfunc', fermi, 0, 100, 4)
fitf.SetParNames('#epsilon', "#mu", '#sigma')
fitf.SetParameters(1,25,2,1)



c = newCanvas()
fitf.Draw()
c.Draw()


In [41]:
ROOT.TVirtualFitter.SetDefaultFitter("Fumili2")
ROOT.TVirtualFitter.SetPrecision(1e-04)

points = []


for pu in ['PU0', 'PU200']:
    for tp in ['DEF', 'DEFCalib', 'DEFMerged']:
        for pt in [10, 20, 30]:
                tp_sel = 'EmPt{}'.format(pt)
                hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, tp, tp_sel, 'GENEtaBC')
                # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
                h_eff_vs_pt = [his.h_ton.h_pt.CreateGraph() for his in hsets]
                tf_yc.SetParameters(1, 20, 4, 1.0, 0.0);
                result = h_eff_vs_pt[0].Fit(tf_yc, 'MQRS+')
                print '------- {}'.format( text)
                print result.Print()
                pt095 = tf_yc.GetX(0.95)
                points.append((tp, pu, pt, pt095))
                drawSame(h_eff_vs_pt, labels, text=text, min_y=0, max_y=1.1, y_axis_label='L1 matched to GEN and p_{T}>th./L1 matched to GEN', h_lines=[0.95, 1])
                ROOT.gStyle.SetOptFit(11111)

------- PU0, NNDR, EGId, p_{T}^{L1}>=10GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR, EGId, p_{T}^{L1}>=20GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR, EGId, p_{T}^{L1}>=30GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR Calib v1, EGId, p_{T}^{L1}>=10GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR Calib v1, EGId, p_{T}^{L1}>=20GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR Calib v1, EGId, p_{T}^{L1}>=30GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR(merged), EGId, p_{T}^{L1}>=10GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR(merged), EGId, p_{T}^{L1}>=20GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR(merged), EGId, p_{T}^{L1}>=30GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR, EGId, p_{T}^{L1}>=10GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR, EGId, p_{T}^{L1}>=20GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR, EGId, p_{T}^{L1}>=30GeV, 1.52 < |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR Calib v1, E

In [42]:
points

[('DEF', 'PU0', 10, 20.807365559018535),
 ('DEF', 'PU0', 20, 33.721241292170504),
 ('DEF', 'PU0', 30, 45.73862847187145),
 ('DEFCalib', 'PU0', 10, 18.603662878386885),
 ('DEFCalib', 'PU0', 20, 32.79539176259113),
 ('DEFCalib', 'PU0', 30, 44.48343760171104),
 ('DEFMerged', 'PU0', 10, 18.555819036585337),
 ('DEFMerged', 'PU0', 20, 30.723757850027972),
 ('DEFMerged', 'PU0', 30, 40.95332979637703),
 ('DEF', 'PU200', 10, 20.517987030908284),
 ('DEF', 'PU200', 20, 32.72425709742334),
 ('DEF', 'PU200', 30, 45.26997748947073),
 ('DEFCalib', 'PU200', 10, 18.675569839665275),
 ('DEFCalib', 'PU200', 20, 31.905689889341247),
 ('DEFCalib', 'PU200', 30, 44.19045643939614),
 ('DEFMerged', 'PU200', 10, 18.474830587228034),
 ('DEFMerged', 'PU200', 20, 30.08925581332338),
 ('DEFMerged', 'PU200', 30, 40.427929190003624)]

In [52]:
# print points

points_calib_pu0 = [point for point in points if ('Calib' in point[0] and 'PU0' in point[1])]
points_calib_pu200 = [point for point in points if ( 'Calib' in point[0] and 'PU200' in point[1])]

points_nocalib_pu0 = [point for point in points if (point[0]=='DEF' and 'PU0' in point[1])]
points_nocalib_pu200 = [point for point in points if (point[0]=='DEF' and 'PU200' in point[1])]

points_merged_pu0 = [point for point in points if (point[0]=='DEFMerged' and 'PU0' in point[1])]
points_merged_pu200 = [point for point in points if (point[0]=='DEFMerged' and 'PU200' in point[1])]

# print points
# print points_calib_pu0
# print points_calib_pu200
# print points_nocalib_pu0
# print points_nocalib_pu200

def drawScaling(points, label, text):
    graph =  ROOT.TGraph(len(points), array('d', [point[2] for point in points]), array('d',[point[3] for point in points]))
    drawGraphsSame([graph], labels=[label], min_y=0, max_y=50, options='A*', text=text)
    graph.Fit('pol1', 'S')
    
    ROOT.gStyle.SetOptFit(11111)
    return graph

g1 = drawScaling(points=points_nocalib_pu0, label='PU0', text='PU0: no calib')
g3 = drawScaling(points=points_calib_pu0, label='PU0', text='PU0: calib')
g5 = drawScaling(points=points_merged_pu0, label='PU0', text='PU0: merged')

g2 = drawScaling(points=points_nocalib_pu200, label='PU200', text='PU200: no calib')
g4 = drawScaling(points=points_calib_pu200, label='PU200', text='PU200: calib')
g6 = drawScaling(points=points_merged_pu200, label='PU200', text='PU200: merged')


# graph_nocalib_pu0 = ROOT.TGraph(len(points_nocalib_pu0), array('d', [point[2] for point in points_nocalib_pu0]), array('d',[point[3] for point in points_nocalib_pu0]))
# drawGraphsSame([graph_nocalib_pu0], labels=['PU0'], min_y=0, max_y=50, options='A*', text='no calib')
# graph_nocalib_pu0.Fit('pol1', 'S')
# ROOT.gStyle.SetOptFit(11111)

# graph_calib_pu0 = ROOT.TGraph(len(points_calib_pu0), array('d', [point[2] for point in points_calib_pu0]), array('d',[point[3] for point in points_calib_pu0]))
# drawGraphsSame([graph_calib_pu0], labels=['PU0'], min_y=0, max_y=50, options='A*', text='calib')
# graph_calib_pu0.Fit('pol1', 'S')
# ROOT.gStyle.SetOptFit(11111)


# graph_nocalib_pu200 = ROOT.TGraph(len(points_nocalib_pu200), array('d', [point[2] for point in points_nocalib_pu200]), array('d',[point[3] for point in points_nocalib_pu200]))
# drawGraphsSame([graph_nocalib_pu200], labels=['PU200'], min_y=0, max_y=50, options='A*', text='no calib')
# graph_nocalib_pu200.Fit('pol1', 'S')
# ROOT.gStyle.SetOptFit(11111)

# graph_calib_pu200 = ROOT.TGraph(len(points_calib_pu200), array('d', [point[2] for point in points_calib_pu200]), array('d',[point[3] for point in points_calib_pu200]))
# drawGraphsSame([graph_calib_pu200], labels=['PU200'], min_y=0, max_y=50, options='A*', text='calib')
# graph_calib_pu200.Fit('pol1', 'S')
# ROOT.gStyle.SetOptFit(11111)


****************************************
Minimizer is Linear
Chi2                      =     0.133949
NDf                       =            1
p0                        =      8.49115   +/-   0.559059    
p1                        =      1.24656   +/-   0.0258794   

****************************************
Minimizer is Linear
Chi2                      =      1.04474
NDf                       =            1
p0                        =      6.08106   +/-   1.56132     
p1                        =      1.29399   +/-   0.0722751   

****************************************
Minimizer is Linear
Chi2                      =     0.626211
NDf                       =            1
p0                        =      7.68012   +/-   1.20878     
p1                        =      1.11988   +/-   0.0559558   

****************************************
Minimizer is Linear
Chi2                      =    0.0192044
NDf                       =            1
p0                        =      8.08542   +/-   0.2

In [27]:
points = []


for pu in ['PU0', 'PU200']:
    for tp in ['DEF', 'DEFCalib']:
        for pt in [10, 20, 25, 30]:
                tp_sel = 'EmPt{}'.format(pt)
                hsets, labels, text = hplot.get_histo(histos.HistoSetEff, 'ele', pu, tp, tp_sel, 'GENEtaABC')
                # drawSeveral([his.hreso.h_ptResVpt for his in hsets], labels,  'COLZ', do_profile=True, text=text)
                h_eff_vs_pt = [his.h_ton.h_pt.CreateGraph() for his in hsets]
                tf_yc.SetParameters(1, 20, 4, 1.0, 0.0);
                result = h_eff_vs_pt[0].Fit(tf_yc, 'MQRS+')
                print '------- {}'.format( text)
                print result.Print()
                pt095 = tf_yc.GetX(0.95)
                points.append((tp, pu, pt, pt095))
                drawSame(h_eff_vs_pt, labels, text=text, min_y=0, max_y=1.1, y_axis_label='L1 matched to GEN and p_{T}>th./L1 matched to GEN', h_lines=[0.95, 1])
                ROOT.gStyle.SetOptFit(11111)

------- PU0, NNDR, EGId, p_{T}^{L1}>=10GeV, |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR, EGId, p_{T}^{L1}>=20GeV, |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR, EGId, p_{T}^{L1}>=25GeV, |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR, EGId, p_{T}^{L1}>=30GeV, |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR Calib v1, EGId, p_{T}^{L1}>=10GeV, |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR Calib v1, EGId, p_{T}^{L1}>=20GeV, |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR Calib v1, EGId, p_{T}^{L1}>=25GeV, |#eta^{GEN}| <= 2.4
None
------- PU0, NNDR Calib v1, EGId, p_{T}^{L1}>=30GeV, |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR, EGId, p_{T}^{L1}>=10GeV, |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR, EGId, p_{T}^{L1}>=20GeV, |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR, EGId, p_{T}^{L1}>=25GeV, |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR, EGId, p_{T}^{L1}>=30GeV, |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR Calib v1, EGId, p_{T}^{L1}>=10GeV, |#eta^{GEN}| <= 2.4
None
------- PU200, NNDR Calib v1, EGId, p_{T}^{L1}>=

In [28]:
points_calib_pu0 = [point for point in points if ('Calib' in point[0] and 'PU0' in point[1])]
points_calib_pu200 = [point for point in points if ( 'Calib' in point[0] and 'PU200' in point[1])]

points_nocalib_pu0 = [point for point in points if ('Calib' not in point[0] and 'PU0' in point[1])]
points_nocalib_pu200 = [point for point in points if ( 'Calib' not in point[0] and 'PU200' in point[1])]

print points
# print points_calib_pu0
# print points_calib_pu200
# print points_nocalib_pu0
# print points_nocalib_pu200

graph_nocalib_pu0 = ROOT.TGraph(len(points_nocalib_pu0), array('d', [point[2] for point in points_nocalib_pu0]), array('d',[point[3] for point in points_nocalib_pu0]))
drawGraphsSame([graph_nocalib_pu0], labels=['PU0'], min_y=0, max_y=50, options='A*', text='no calib')
graph_nocalib_pu0.Fit('pol1', 'S')
ROOT.gStyle.SetOptFit(11111)

graph_calib_pu0 = ROOT.TGraph(len(points_calib_pu0), array('d', [point[2] for point in points_calib_pu0]), array('d',[point[3] for point in points_calib_pu0]))
drawGraphsSame([graph_calib_pu0], labels=['PU0'], min_y=0, max_y=50, options='A*', text='calib')
graph_calib_pu0.Fit('pol1', 'S')
ROOT.gStyle.SetOptFit(11111)


graph_nocalib_pu200 = ROOT.TGraph(len(points_nocalib_pu200), array('d', [point[2] for point in points_nocalib_pu200]), array('d',[point[3] for point in points_nocalib_pu200]))
drawGraphsSame([graph_nocalib_pu200], labels=['PU200'], min_y=0, max_y=50, options='A*', text='no calib')
graph_nocalib_pu200.Fit('pol1', 'S')
ROOT.gStyle.SetOptFit(11111)

graph_calib_pu200 = ROOT.TGraph(len(points_calib_pu200), array('d', [point[2] for point in points_calib_pu200]), array('d',[point[3] for point in points_calib_pu200]))
drawGraphsSame([graph_calib_pu200], labels=['PU200'], min_y=0, max_y=50, options='A*', text='calib')
graph_calib_pu200.Fit('pol1', 'S')
ROOT.gStyle.SetOptFit(11111)

[('DEF', 'PU0', 10, 22.3534494344717), ('DEF', 'PU0', 20, 36.783019374488724), ('DEF', 'PU0', 25, 43.10413863859281), ('DEF', 'PU0', 30, 49.06314741463852), ('DEFCalib', 'PU0', 10, 19.99474332507898), ('DEFCalib', 'PU0', 20, 35.032866502257924), ('DEFCalib', 'PU0', 25, 41.588832113720144), ('DEFCalib', 'PU0', 30, 47.269526958522974), ('DEF', 'PU200', 10, 23.32041951835891), ('DEF', 'PU200', 20, 37.892364844376395), ('DEF', 'PU200', 25, 44.483653708017854), ('DEF', 'PU200', 30, 50.380391686270876), ('DEFCalib', 'PU200', 10, 20.887989501408413), ('DEFCalib', 'PU200', 20, 36.22727094680916), ('DEFCalib', 'PU200', 25, 42.88157597889916), ('DEFCalib', 'PU200', 30, 48.982961197277426)]

****************************************
Minimizer is Linear
Chi2                      =     0.858972
NDf                       =            2
p0                        =      9.31568   +/-   0.996972    
p1                        =      1.34166   +/-   0.0443099   

****************************************
M

In [29]:

samples = samples_ele
tp_sets = ['DEF', 'DEF_em', 'DEF_pt20', 'DEF_pt20_em', 'DEF_pt25', 'DEF_pt25_em', 'DEF_pt30', 'DEF_pt30_em']
particles = ['ele', 'eleA', 'eleB', 'eleC', 'eleD', 'eleAAA', 'eleAA', 'eleBB', 'eleCC', 'eleDD']


labels = [sample.label for sample in samples]




histo_df = pd.DataFrame(index=tp_sets, columns=particles)
histo_num_df = pd.DataFrame(index=tp_sets, columns=particles)
histo_den_df = pd.DataFrame(index=tp_sets, columns=particles)
titles_df = pd.DataFrame(index=tp_sets, columns=particles)
# print histo_num_df
for tp_set in tp_sets:
    for particle in particles:
        histo_df.loc[tp_set][particle] =  [histos.HistoSetEff('{}_{}'.format(tp_set, particle), sample.histo_file).h_eff for sample in samples]
        histo_num_df.loc[tp_set][particle] = [histos.HistoSetEff('{}_{}'.format(tp_set, particle), sample.histo_file).h_num for sample in samples]
        histo_den_df.loc[tp_set][particle] = [histos.HistoSetEff('{}_{}'.format(tp_set, particle), sample.histo_file).h_den for sample in samples]

        titles_df.loc[tp_set, particle] = '{}, {}'.format(tpset_labels[tp_set], particle_labels[particle])

histo_df



NameError: name 'tpset_labels' is not defined

In [ ]:
titles_df

In [ ]:
dir(histo_df.ele['DEF'][0])


In [ ]:
histo_df.loc['DEF', 'ele']

In [ ]:

for particle in ['ele']:
    for tp_set in tp_sets:
        h_eff_vs_eta = [histo.h_eta.CreateGraph() for histo in histo_df.ele[tp_set]]
        drawGraphsSame(h_eff_vs_eta, labels, text=titles_df.loc[tp_set, particle])



In [ ]:
line095 = ROOT.TLine(0,0.95,110,0.95)
line095.SetLineStyle(2)
for particle in particles:
    for tp_set in tp_sets:
        #print 'particle: {}, TP set: {}, text: {}'.format(particle, tp_set, titles_df.loc[tp_set, particle])
        h_eff_vs_pt = [histo.h_pt.CreateGraph() for histo in histo_df.loc[tp_set, particle]]
        drawGraphsSame(h_eff_vs_pt, labels, text=titles_df.loc[tp_set, particle], min_y=0., max_y=1.1)
        line095.Draw('same')

In [ ]:
histo_den_df

In [ ]:
# build turnon

for particle in particles:
    TP_set_den = 'DEF' # -> L1 matched/GEN
    TP_set_num_l = ['DEF_pt20', 'DEF_pt25', 'DEF_pt30'] # -> L1 matched & above threshols / GEN
    
    histo_den = [histo for histo in histo_num_df.loc[TP_set_den][particle]] # -> L1 matched
    for TP_set_num in TP_set_num_l:
        histo_num = [histo for histo in histo_num_df.loc[TP_set_num][particle]] # -> L1 matched & above threshols

        histos_turnon = []
        for idx,histo_num in enumerate(histo_num):
            histo_turnon_num = histo_num.h_pt.Clone(uuid.uuid4().hex[:6])
            stuff.append(histo_turnon_num)
            histo_turnon_den = histo_den[idx].h_pt.Clone(uuid.uuid4().hex[:6])
            stuff.append(histo_turnon_den)
            hton = ROOT.TEfficiency(histo_turnon_num, histo_turnon_den)
            stuff.append(hton)
            histos_turnon.append(hton)
        drawGraphsSame(histos_turnon, labels, text=titles_df.loc[TP_set_num, particle])

In [ ]:
for particle in particles:
    TP_set_den = 'DEF_em' # -> L1 matched/GEN
    TP_set_num_l = ['DEF_pt20_em', 'DEF_pt25_em', 'DEF_pt30_em'] # -> L1 matched & above threshols / GEN
    
    histo_den = [histo for histo in histo_num_df.loc[TP_set_den][particle]] # -> L1 matched
    for TP_set_num in TP_set_num_l:
        histo_num = [histo for histo in histo_num_df.loc[TP_set_num][particle]] # -> L1 matched & above threshols

        histos_turnon = []
        for idx,histo_num in enumerate(histo_num):
            histo_turnon_num = histo_num.h_pt.Clone(uuid.uuid4().hex[:6])
            stuff.append(histo_turnon_num)
            histo_turnon_den = histo_den[idx].h_pt.Clone(uuid.uuid4().hex[:6])
            stuff.append(histo_turnon_den)
            hton = ROOT.TEfficiency(histo_turnon_num, histo_turnon_den)
            stuff.append(hton)
            histos_turnon.append(hton)
        drawGraphsSame(histos_turnon, labels, text=titles_df.loc[TP_set_num, particle])

# Photon pt35 GeV 1.6 < |eta| < 2.8 

In [ ]:

samples = samples_photon
tp_sets = ['DEF', 'DEF_em']
particles = ['photon']
labels = [sample.label for sample in samples]

histo_df = pd.DataFrame(index=tp_sets, columns=particles)
histo_num_df = pd.DataFrame(index=tp_sets, columns=particles)
histo_den_df = pd.DataFrame(index=tp_sets, columns=particles)

for tp_set in tp_sets:
    for particle in particles:
        histo_df.loc[tp_set][particle] =  [histos.HistoSetEff('{}_{}'.format(tp_set, particle), sample.histo_file).h_eff for sample in samples]
        histo_num_df[tp_set][particle] = [histos.HistoSetEff('{}_{}'.format(tp_set, particle), sample.histo_file).h_num for sample in samples]
        histo_den_df[tp_set][particle] = [histos.HistoSetEff('{}_{}'.format(tp_set, particle), sample.histo_file).h_den for sample in samples]

        histo_df



In [ ]:
dir(histo_df.photon['DEF'][0])


In [ ]:
tp_set = 'DEF'
h_eff_vs_eta = [histo.h_eta.CreateGraph() for histo in histo_df.photon[tp_set]]
drawGraphsSame(h_eff_vs_eta, labels)

tp_set = 'DEF_em'
h_eff_vs_eta = [histo.h_eta.CreateGraph() for histo in histo_df.photon[tp_set]]
drawGraphsSame(h_eff_vs_eta, labels)
